# <------------ Non Reusable Code (change 3 variables per season)---------------->

In [1]:
season="S11"
web_url_containing_images="https://lilablobssc.blob.core.windows.net/snapshotserengeti-v-2-0/SnapshotSerengetiS11.json.zip"
metadata_storage_location="C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\SnapshotSerengetiS11.json.zip"

# <--------Reusable Code (no need to change anything for all seasons---------->

# Setting the working directory to be the project folder location

In [2]:
import os
notebook_And_Data_Storage_Location='C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat'
os.chdir(notebook_And_Data_Storage_Location)  # changes the directory to point to the our project folder
os.getcwd() #showing the file path for the folder in which this notebook is stored on my pc

'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat'

In [3]:
os.listdir(notebook_And_Data_Storage_Location) # see the project folders contents

['.ipynb_checkpoints',
 'DataPreprocessor.ipynb',
 'elephant_clean',
 'imageDataset',
 'impala_clean',
 'SnapshotSerengetiS11.json',
 'SnapshotSerengetiS11.json.zip',
 'zebra_clean']

# Downloading the Dataset

In [4]:
#--------------GIVEN CODE---------------#
#SOURCE: https://github.com/microsoft/CameraTraps/blob/master/data_management/download_lila_subset.py
sas_url = 'https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped?st=2020-01-01T00%3A00%3A00Z&se=2034-01-01T00%3A00%3A00Z&sp=rl&sv=2019-07-07&sr=c&sig=/DGPd%2B9WGFt6HgkemDFpo2n0M1htEXvTq9WoHlaH7L4%3D'
base_url = sas_url.split('?')[0]
print(base_url)
sas_token = sas_url.split('?')[1]
print(sas_token)

https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped
st=2020-01-01T00%3A00%3A00Z&se=2034-01-01T00%3A00%3A00Z&sp=rl&sv=2019-07-07&sr=c&sig=/DGPd%2B9WGFt6HgkemDFpo2n0M1htEXvTq9WoHlaH7L4%3D


In [5]:
#--------------GIVEN CODE---------------#
#SOURCE: https://github.com/microsoft/CameraTraps/blob/master/data_management/download_lila_subset.py
import urllib.request

def download_image(fn, species, directory, overwrite_files):
    try: 
        url = base_url + '/' + fn
        target_file = os.path.join(directory,fn)

        if ((not overwrite_files) and (os.path.isfile(target_file))):
            print('Skipping file {}'.format(fn))
            return
        
        print("getting image from: {}", format(url))
        print("saving image into: {}", format(target_file))
        os.makedirs(os.path.dirname(target_file),exist_ok=True)
        urllib.request.urlretrieve(url,target_file)
    except Exception as ex:
        print("Failed to download images")

In [6]:
#--------------GIVEN CODE---------------#
#SOURCE: https://github.com/microsoft/CameraTraps/blob/master/data_management/download_lila_subset.py

import os
import json
from tqdm import tqdm
from multiprocessing.pool import ThreadPool

def download_images_per_season(species):
    json_filename = r"SnapshotSerengetiS11.json"
    print("........reading " + json_filename)
    
    output_dir = f'imageDataset/{species}'    
    print("........all images are saved @ location:  " + output_dir)
    
    species_of_interest = species
    
    # We will demonstrate two approaches to downloading, one that loops over files
    # and downloads directly in Python, another that uses AzCopy.
    # AzCopy will generally be more performant and supports resuming if the 
    # transfers are interrupted.  It assumes that azcopy is on the system path.
    use_azcopy_for_download = False
    n_download_threads = 1
    
    overwrite_files = True
       
    # Open the metadata file
    with open(json_filename, 'r') as f:
        data = json.load(f)
        
    categories = data['categories']
    annotations = data['annotations']
    images = data['images']

    #%% Build a list of image files (relative path names) that match the target species

    # Retrieve the category ID we're interested in
    category_of_interest = list(filter(lambda x: x['name'] == species_of_interest, categories))
    assert len(category_of_interest) == 1
    category_of_interest = category_of_interest[0]
    category_id_of_interest = category_of_interest['id']
    
    # Retrieve all the images that match that category
    image_ids_of_interest = set([ann['image_id'] 
                                 for ann in annotations 
                                 if ann['category_id'] == category_id_of_interest])
    
    print('Selected {} of {} images'.format(len(image_ids_of_interest),len(images)))

     # Retrieve image file names
    filenames = [im['file_name'] 
                 for im in images 
                 if im['id'] in image_ids_of_interest]
    assert len(filenames) == len(image_ids_of_interest)

    # Loop over files
    print('Downloading images for {0} without azcopy'.format(species_of_interest))
    
    if n_download_threads <= 1:
    
        for fn in tqdm(filenames):  
            try:      
                download_image(fn, species,output_dir, overwrite_files) # function call
            except Exception as ex:
                print(ex)        
    else:
    
        pool = ThreadPool(n_download_threads)        
        tqdm(pool.imap(download_image, filenames), total=len(filenames))

In [7]:
#coding the function (not given aka its a custom function)
import wget

def get_the_zipped_metadata_from_the_website_and_store_it_in_the_project_folder():
    UrlForZippedMetadata=web_url_containing_images
    wget.download(web_url_containing_images)#savingTheZippedMetaDataIntoProjectFolder

In [8]:
#coding the function (not given aka its a custom function)
import zipfile

filePathWhereZippedMetadataIsLocated = metadata_storage_location
filePathWhereTheUnZippedMetadataWillBeStored = "C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat"

def unzip_the_zipped_metadata_and_store_it_in_the_project_folder():
    with zipfile.ZipFile(filePathWhereZippedMetadataIsLocated, 'r') as zip_ref:
        zip_ref.extractall(filePathWhereTheUnZippedMetadataWillBeStored)

In [9]:
#coding the function (not given aka its a custom function)
def moving_nested_images_to_the_root_level_of_the_species_folder(sourceFolder,season):
    #2nd, we get a list of all the images in the subfolders
    import glob, shutil
    listofImages=glob.glob(sourceFolder+"/**/*.jpg", recursive=True)

    print("\n")
    print(listofImages)

    print("\n")
    for image in listofImages:
        print(image)
    print("\n")

    #3rd, we iterates through all the images and move them into the destination folder
    for image in listofImages:
        print("moving image from {} to {}".format(image,sourceFolder))
        shutil.move(image,sourceFolder)
    
    #4th,deleting the non-empty subfolders within the species folder       
    folder_to_delete=sourceFolder+"\\"+season
    shutil.rmtree(folder_to_delete)

In [11]:
#function call
get_the_zipped_metadata_from_the_website_and_store_it_in_the_project_folder()

100% [........................................................................] 24463908 / 24463908

In [12]:
#function call
unzip_the_zipped_metadata_and_store_it_in_the_project_folder()

# Downloading elephant images for a particular season

In [12]:
#function call
download_images_per_season("elephant") 

........reading SnapshotSerengetiS11.json
........all images are saved @ location:  imageDataset/elephant


  0%|                                                                                         | 0/3745 [00:00<?, ?it/s]

Selected 3745 of 499401 images
getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/K10/K10_R1/SER_S11_K10_R1_IMAG0171.JPG
saving image into: {} imageDataset/elephant\SER_S11/K10/K10_R1/SER_S11_K10_R1_IMAG0171.JPG


  0%|                                                                                 | 1/3745 [00:00<50:20,  1.24it/s]

getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/K10/K10_R1/SER_S11_K10_R1_IMAG0075.JPG
saving image into: {} imageDataset/elephant\SER_S11/K10/K10_R1/SER_S11_K10_R1_IMAG0075.JPG


...

 51%|████████████████████████████████████████                                      | 1925/3745 [26:33<24:16,  1.25it/s]

getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/C13/C13_R1/SER_S11_C13_R1_IMAG2243.JPG
saving image into: {} imageDataset/elephant\SER_S11/C13/C13_R1/SER_S11_C13_R1_IMAG2243.JPG


 51%|████████████████████████████████████████                                      | 1926/3745 [26:33<22:10,  1.37it/s]

getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/K10/K10_R1/SER_S11_K10_R1_IMAG0201.JPG
saving image into: {} imageDataset/elephant\SER_S11/K10/K10_R1/SER_S11_K10_R1_IMAG0201.JPG


KeyboardInterrupt: 

# Moving nested images to the root level of the species folders

In [11]:
elephantFolder = "C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\elephant"
impalaFolder = "C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\impala"
zebraFolder = "C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\zebra"

In [14]:
#function call
moving_nested_images_to_the_root_level_of_the_species_folder(elephantFolder,season)



['C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\elephant\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0025.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\elephant\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0026.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\elephant\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0027.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\elephant\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0028.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\elephant\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0030.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\elephant\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0031.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\elephant\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0032.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\elephant\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0036.JPG', 'C:\\

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\C05\C05_R2\SER_S11_C05_R2_IMAG2754.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\C05\C05_R2\SER_S11_C05_R2_IMAG2755.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\C08\C08_R1\SER_S11_C08_R1_IMAG0115.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\C08\C08_R1\SER_S11_C08_R1_IMAG0116.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\C08\C08_R1\SER_S11_C08_R1_IMAG0117.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\E02\E02_R2\SER_S11_E02_R2_IMAG0041.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\E02\E02_R2\SER_S11_E02_R2_IMAG0042.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\E02\E02_R2\SER_S11_E02_R2_IMAG0043.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\E02\E02_R2\SER_S11_E02_R2_IMAG0596.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\E02\E02_R2\SER_S11_E02_R2_IMAG0618.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\F07\F07_R1\SER_S11_F07_R1_IMAG0081.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\F07\F07_R1\SER_S11_F07_R1_IMAG0082.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\F07\F07_R1\SER_S11_F07_R1_IMAG0090.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\F07\F07_R1\SER_S11_F07_R1_IMAG0091.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\F07\F07_R1\SER_S11_F07_R1_IMAG0170.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\H06\H06_R1\SER_S11_H06_R1_IMAG0343.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\H06\H06_R1\SER_S11_H06_R1_IMAG0344.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\H06\H06_R1\SER_S11_H06_R1_IMAG0349.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\H06\H06_R1\SER_S11_H06_R1_IMAG0354.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\H06\H06_R1\SER_S11_H06_R1_IMAG0355.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\I06\I06_R2\SER_S11_I06_R2_IMAG0033.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\I06\I06_R2\SER_S11_I06_R2_IMAG0114.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\I06\I06_R2\SER_S11_I06_R2_IMAG0116.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\I06\I06_R2\SER_S11_I06_R2_IMAG0117.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\I06\I06_R2\SER_S11_I06_R2_IMAG0267.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\J09\J09_R2\SER_S11_J09_R2_IMAG0068.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\J09\J09_R2\SER_S11_J09_R2_IMAG0069.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\J09\J09_R2\SER_S11_J09_R2_IMAG0071.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\J09\J09_R2\SER_S11_J09_R2_IMAG0274.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\J09\J09_R2\SER_S11_J09_R2_IMAG0275.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\K10\K10_R1\SER_S11_K10_R1_IMAG0230.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\K10\K10_R1\SER_S11_K10_R1_IMAG0231.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\K10\K10_R1\SER_S11_K10_R1_IMAG0234.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\K10\K10_R1\SER_S11_K10_R1_IMAG0236.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\K10\K10_R1\SER_S11_K10_R1_IMAG0237.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\M07\M07_R2\SER_S11_M07_R2_IMAG0839.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\M07\M07_R2\SER_S11_M07_R2_IMAG0842.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\M07\M07_R2\SER_S11_M07_R2_IMAG0843.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\M07\M07_R2\SER_S11_M07_R2_IMAG0844.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11\M07\M07_R2\SER_S11_M07_R2_IMAG0845.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant
moving image from C:

FileNotFoundError: [WinError 3] The system cannot find the path specified: 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\elephant\\S11'

# Downloading impala images for a particular season

In [15]:
#function call
download_images_per_season("impala")

........reading SnapshotSerengetiS11.json
........all images are saved @ location:  imageDataset/impala



  0%|                                                                                         | 0/1485 [00:00<?, ?it/s]

Selected 1485 of 499401 images
getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/H01/H01_R2/SER_S11_H01_R2_IMAG0211.JPG
saving image into: {} imageDataset/impala\SER_S11/H01/H01_R2/SER_S11_H01_R2_IMAG0211.JPG



  0%|                                                                                 | 1/1485 [00:00<14:32,  1.70it/s]

getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/E02/E02_R2/SER_S11_E02_R2_IMAG0838.JPG
saving image into: {} imageDataset/impala\SER_S11/E02/E02_R2/SER_S11_E02_R2_IMAG0838.JPG


...


 68%|████████████████████████████████████████████████████▋                         | 1003/1485 [15:12<06:11,  1.30it/s]

getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/K03/K03_R2/SER_S11_K03_R2_IMAG0492.JPG
saving image into: {} imageDataset/impala\SER_S11/K03/K03_R2/SER_S11_K03_R2_IMAG0492.JPG



 68%|████████████████████████████████████████████████████▋                         | 1004/1485 [15:12<05:54,  1.36it/s]

getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/B03/B03_R1/SER_S11_B03_R1_IMAG0227.JPG
saving image into: {} imageDataset/impala\SER_S11/B03/B03_R1/SER_S11_B03_R1_IMAG0227.JPG


KeyboardInterrupt: 

# Moving nested images to the root level of the species folders

In [16]:
#function call
moving_nested_images_to_the_root_level_of_the_species_folder(impalaFolder,season)



['C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\impala\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0173.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\impala\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0174.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\impala\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0175.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\impala\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0176.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\impala\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0177.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\impala\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0227.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\impala\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0229.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\impala\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0232.JPG', 'C:\\Users\\17637\\De

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\E02\E02_R1\SER_S11_E02_R1_IMAG0714.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\E02\E02_R1\SER_S11_E02_R1_IMAG0715.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\E02\E02_R1\SER_S11_E02_R1_IMAG0718.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\E02\E02_R1\SER_S11_E02_R1_IMAG0720.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\E02\E02_R1\SER_S11_E02_R1_IMAG0721.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\E04\E04_R2\SER_S11_E04_R2_IMAG0335.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\E04\E04_R2\SER_S11_E04_R2_IMAG0338.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\E04\E04_R2\SER_S11_E04_R2_IMAG0339.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\E04\E04_R2\SER_S11_E04_R2_IMAG0340.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\E04\E04_R2\SER_S11_E04_R2_IMAG0351.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\H03\H03_R2\SER_S11_H03_R2_IMAG0066.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\H03\H03_R2\SER_S11_H03_R2_IMAG0067.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\H03\H03_R2\SER_S11_H03_R2_IMAG0068.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\H03\H03_R2\SER_S11_H03_R2_IMAG0069.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11\H03\H03_R2\SER_S11_H03_R2_IMAG0070.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala
moving image from C:\Users\17637\Desktop

FileNotFoundError: [WinError 3] The system cannot find the path specified: 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\impala\\S11'

# Downloading zebra images for a particular season

In [21]:
#function call
download_images_per_season("zebra")

........reading SnapshotSerengetiS11.json
........all images are saved @ location:  imageDataset/zebra


  0%|                                                                                        | 0/17533 [00:00<?, ?it/s]

Selected 17533 of 499401 images
getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/E10/E10_R2/SER_S11_E10_R2_IMAG0326.JPG
saving image into: {} imageDataset/zebra\SER_S11/E10/E10_R2/SER_S11_E10_R2_IMAG0326.JPG


  0%|                                                                              | 1/17533 [00:00<3:59:08,  1.22it/s]

getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/D12/D12_R2/SER_S11_D12_R2_IMAG0299.JPG
saving image into: {} imageDataset/zebra\SER_S11/D12/D12_R2/SER_S11_D12_R2_IMAG0299.JPG


...

 12%|████████▋                                                                  | 2043/17533 [29:27<3:56:55,  1.09it/s]

getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/D03/D03_R1/SER_S11_D03_R1_IMAG0498.JPG
saving image into: {} imageDataset/zebra\SER_S11/D03/D03_R1/SER_S11_D03_R1_IMAG0498.JPG


 12%|████████▋                                                                  | 2044/17533 [29:27<3:33:06,  1.21it/s]

getting image from: {} https://lilablobssc.blob.core.windows.net/snapshotserengeti-unzipped/SER_S11/G04/G04_R1/SER_S11_G04_R1_IMAG0274.JPG
saving image into: {} imageDataset/zebra\SER_S11/G04/G04_R1/SER_S11_G04_R1_IMAG0274.JPG


KeyboardInterrupt: 

# Moving nested images to the root level of the species folders

In [22]:
#function call
moving_nested_images_to_the_root_level_of_the_species_folder(zebraFolder,season)



['C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\zebra\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0015.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\zebra\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0020.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\zebra\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0021.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\zebra\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0077.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\zebra\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0083.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\zebra\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0122.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\zebra\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0134.JPG', 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\zebra\\SER_S11\\B03\\B03_R1\\SER_S11_B03_R1_IMAG0154.JPG', 'C:\\Users\\17637\\Desktop\\A

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\C02\C02_R1\SER_S11_C02_R1_IMAG1279.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\C02\C02_R1\SER_S11_C02_R1_IMAG1280.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\C02\C02_R1\SER_S11_C02_R1_IMAG1281.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\C02\C02_R1\SER_S11_C02_R1_IMAG1285.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\C02\C02_R1\SER_S11_C02_R1_IMAG1298.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Projec

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\D03\D03_R1\SER_S11_D03_R1_IMAG1632.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\D03\D03_R1\SER_S11_D03_R1_IMAG1640.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\D03\D03_R2\SER_S11_D03_R2_IMAG0010.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\D03\D03_R2\SER_S11_D03_R2_IMAG0047.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\D03\D03_R2\SER_S11_D03_R2_IMAG0064.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Projec

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\F02\F02_R1\SER_S11_F02_R1_IMAG0206.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\F02\F02_R1\SER_S11_F02_R1_IMAG0215.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\F02\F02_R1\SER_S11_F02_R1_IMAG0218.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\F02\F02_R1\SER_S11_F02_R1_IMAG0229.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\F02\F02_R1\SER_S11_F02_R1_IMAG0238.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Projec

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\G03\G03_R1\SER_S11_G03_R1_IMAG1921.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\G03\G03_R1\SER_S11_G03_R1_IMAG1964.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\G03\G03_R1\SER_S11_G03_R1_IMAG2011.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\G03\G03_R1\SER_S11_G03_R1_IMAG2018.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\G03\G03_R1\SER_S11_G03_R1_IMAG2032.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Projec

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\H02\H02_R1\SER_S11_H02_R1_IMAG2190.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\H02\H02_R1\SER_S11_H02_R1_IMAG2196.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\H02\H02_R2\SER_S11_H02_R2_IMAG0160.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\H02\H02_R2\SER_S11_H02_R2_IMAG0221.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\H02\H02_R2\SER_S11_H02_R2_IMAG0231.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Projec

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\I13\I13_R1\SER_S11_I13_R1_IMAG2563.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\I13\I13_R1\SER_S11_I13_R1_IMAG2579.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\I13\I13_R1\SER_S11_I13_R1_IMAG2582.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\I13\I13_R1\SER_S11_I13_R1_IMAG2593.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\I13\I13_R1\SER_S11_I13_R1_IMAG2646.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Projec

moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\N12\N12_R2\SER_S11_N12_R2_IMAG0072.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\N12\N12_R2\SER_S11_N12_R2_IMAG0073.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\N12\N12_R2\SER_S11_N12_R2_IMAG0076.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\N12\N12_R2\SER_S11_N12_R2_IMAG0124.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11\O05\O05_R1\SER_S11_O05_R1_IMAG0198.JPG to C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra
moving image from C:\Users\17637\Desktop\AI_Projec

FileNotFoundError: [WinError 3] The system cannot find the path specified: 'C:\\Users\\17637\\Desktop\\AI_Project_Big_Cat\\imageDataset\\zebra\\S11'

# Importing relevant libraries for cleaning images

In [13]:
from PIL import Image,ImageFile
import glob
ImageFile.LOAD_TRUNCATED_IMAGES = True

#coding the function  (not given aka its a custom function)
def image_cropper(filePathForImages):
    #------------------For loop to open the image, crop the image and save the image(* is for wildcard search)--#
    for individualImagesFilePath in glob.glob(filePathForImages):
        image=Image.open(individualImagesFilePath) #opening the image
        print("Original Image Location: ", individualImagesFilePath)
        width, height = image.size #storing images width and height
        print("Original Image Width: ", width)
        print("Original Image Height: ", height)
        croppedImage=image.crop((0,0,width,height-90)) #cropping the image (cutting 9o pixels from the bottom)
        croppedWidth, croppedHeight =  croppedImage.size #storing images width and height
        print("Cropped Image Width: ", croppedWidth)
        print("Cropped Image Height: ",croppedHeight)
        croppedImage.save(individualImagesFilePath) #overwriting the original image with the cropped image
        print("Overwritten Image is Cropped and stored at Location: ", individualImagesFilePath)   

# Cropping images 

##### get rid of the time stamp at the bottom of the images(noise that throws off the classifiers accuracy, precision, recall and AUC values)

In [14]:
#function call
image_cropper(elephantFolder+"\\*.JPG")

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0025.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0025.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0026.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0026.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0027.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image 

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0617.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0619.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0619.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG0778.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG0778.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_

Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG5679.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG5681.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG5681.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG5682.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG5682.JPG
Original Image Location:  C:\Users\17637\Deskto

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C01_R2_IMAG1088.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C01_R2_IMAG1220.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C01_R2_IMAG1220.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C01_R2_IMAG1221.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C01_R2_IMAG1221.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C02_

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_R2_IMAG0059.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_R2_IMAG0060.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_R2_IMAG0060.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_R2_IMAG0063.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_R2_IMAG0063.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_

...

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0800.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0802.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0802.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0803.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0803.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0844.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0845.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0845.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0846.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0846.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_

Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_N05_R1_IMAG0618.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_N05_R1_IMAG0641.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_N05_R1_IMAG0641.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_N05_R1_IMAG0644.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_N05_R1_IMAG0644.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageD

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P06_R2_IMAG1629.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P06_R2_IMAG1630.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P06_R2_IMAG1630.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P11_R2_IMAG1170.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P11_R2_IMAG1170.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P11_

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_R2_IMAG2354.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_R2_IMAG2355.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_R2_IMAG2355.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_R2_IMAG2436.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_R2_IMAG2436.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_

In [15]:
#function call
image_cropper(impalaFolder+"\\*.JPG")

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0173.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0173.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0174.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0174.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0175.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0629.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0629.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0630.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0630.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0631.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped

Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B04_R1_IMAG0231.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B04_R1_IMAG0232.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B04_R1_IMAG0232.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B04_R1_IMAG0234.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B04_R1_IMAG0234.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\imp

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1440.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1445.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1445.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1447.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1447.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1448.

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG2011.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG2015.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG2015.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG2016.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG2016.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG2017.

...

Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_I02_R2_IMAG0461.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_I02_R2_IMAG0466.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_I02_R2_IMAG0466.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_I02_R2_IMAG0468.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_I02_R2_IMAG0468.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\imp

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_J02_R2_IMAG0028.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_J02_R2_IMAG0028.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_J02_R2_IMAG0039.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_J02_R2_IMAG0039.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_J02_R2_IMAG0040.JPG
Original Image Width:  2048
Original Image Height:  1536
Cropped Image Width:  2048
Cropped Image Height:  1446
Overwritten Image is Cropped

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0786.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0787.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0787.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0788.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0788.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0789.

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG1606.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG1606.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG1643.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG1643.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG1645.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_N05_R2_IMAG1057.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_N05_R2_IMAG1859.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_N05_R2_IMAG1859.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_O05_R2_IMAG0039.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_O05_R2_IMAG0039.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_O05_R2_IMAG0040.

In [23]:
#function call
image_cropper(zebraFolder+"\\*.JPG")

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0543.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0543.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0550.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0550.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0551.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and 

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0855.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0857.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0857.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0868.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0868.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0871.JPG
Or

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1532.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1532.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1544.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1544.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1650.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and 

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG2398.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG2411.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG2411.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG2420.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG2420.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG2622.JPG
Or

Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E03_R1_IMAG0175.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E03_R1_IMAG0178.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E03_R1_IMAG0178.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E03_R1_IMAG0190.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E03_R1_IMAG0190.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SE

...

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1712.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1725.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1725.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1734.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1734.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1744.JPG
Or

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1007.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1007.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1014.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1014.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1030.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and 

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1272.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1272.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1277.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1277.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1287.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and 

Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q06_R2_IMAG0634.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q06_R2_IMAG0662.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q06_R2_IMAG0662.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q06_R2_IMAG0669.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q06_R2_IMAG0669.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q06_R2_IMAG0672.JPG
Or

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_R08_R2_IMAG0903.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_R08_R2_IMAG0903.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_R08_R2_IMAG0915.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_R08_R2_IMAG0915.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_R08_R2_IMAG0919.JPG
Original Image Width:  2560
Original Image Height:  1920
Cropped Image Width:  2560
Cropped Image Height:  1830
Overwritten Image is Cropped and 

# Resizing images

#### images get converted into matricies which get updated during backward propogation so smaller images means that we have smaller matricies to update during backward propogation and this is important because when we ran the transfer learning cnn model with the original image size we got a "Resource Exhaustion Error" which basically means that the data structure(tensor) was too big to load into the RAM in order to compute backwardpropogation for training the neural network

In [17]:
#coding the function  (not given aka its a custom function)
def image_resizer(filePathForImages):
    #---------------------For loop to open the image, resize the cropped image and save the image(* is for wildcard search)--#
    for individualImagesFilePath in glob.glob(filePathForImages):
        image=Image.open(individualImagesFilePath) #opening the image
        print("Original Image Location: ", individualImagesFilePath)
        resizedCroppedImage=image.resize((512,361)) #resizing the cropped image to be 512 pixels(width) x 361 pixels(height)
        ResizedCroppedWidth, ResizedCroppedHeight =  resizedCroppedImage.size #storing images width and height
        print("Resized Cropped Image Width: ", ResizedCroppedWidth)
        print("Resized Cropped Image Height: ",ResizedCroppedHeight)
        resizedCroppedImage.save(individualImagesFilePath) #overwriting the original image with the cropped image
        print("Overwritten Resized Cropped Image are stored at Location: ", individualImagesFilePath)   

In [18]:
#function call
image_resizer(elephantFolder+"\\*.JPG")

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0025.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0025.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0026.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0026.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0027.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0617.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0619.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B03_R1_IMAG0619.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG0778.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG0778.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG0779.JPG
Resized Cropped Image Width:  512
Resized Cropped Image

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG5682.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG5683.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG5683.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG6630.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG6630.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_B13_R1_IMAG8304.JPG
Resized Cropped Image Width:  512
Resized Cropped Image

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C02_R2_IMAG0786.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C02_R2_IMAG0790.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C02_R2_IMAG0790.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C02_R2_IMAG0978.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C02_R2_IMAG0978.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C02_R2_IMAG1051.JPG
Resized Cropped Image Width:  512
Resized Cropped Image

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_R2_IMAG0114.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_R2_IMAG0115.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_R2_IMAG0115.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_R2_IMAG0116.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_R2_IMAG0116.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_C03_R2_IMAG0117.JPG
Resized Cropped Image Width:  512
Resized Cropped Image

...

Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0783.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0784.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0784.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0786.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0786.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0832.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0834.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0834.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0838.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0838.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M07_R2_IMAG0839.JPG
Resized Cropped Image Width:  512
Resized Cropped Image

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M13_R2_IMAG2365.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M13_R2_IMAG2366.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M13_R2_IMAG2366.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M13_R2_IMAG3183.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_M13_R2_IMAG3183.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_N05_R1_IMAG0617.JPG
Resized Cropped Image Width:  512
Resized Cropped Image

Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P06_R2_IMAG1626.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P06_R2_IMAG1627.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P06_R2_IMAG1627.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P06_R2_IMAG1629.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P06_R2_IMAG1629.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_P06_R2

Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_R2_IMAG2353.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_R2_IMAG2354.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_R2_IMAG2354.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_R2_IMAG2355.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_R2_IMAG2355.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\elephant\SER_S11_R08_R2

In [19]:
#function call
image_resizer(impalaFolder+"\\*.JPG")

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0173.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0173.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0174.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0174.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0175.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0175.JP

Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0632.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0633.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0633.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0634.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0634.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B03_R1_IMAG0637.JP

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B04_R1_IMAG0280.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B13_R1_IMAG1084.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B13_R1_IMAG1084.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B13_R1_IMAG1086.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B13_R1_IMAG1086.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_B13_R1_IMAG2166.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  36

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1453.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1453.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1454.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1454.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1455.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C02_R2_IMAG1455.JP

Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C13_R1_IMAG2303.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C13_R1_IMAG2304.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C13_R1_IMAG2304.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C13_R1_IMAG2312.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C13_R1_IMAG2312.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_C13_R1_IMAG2313.JPG
Resized Cropped Image Width:  51

...

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_I01_R2_IMAG0109.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_I01_R2_IMAG0155.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_I01_R2_IMAG0155.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_I01_R2_IMAG0156.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_I01_R2_IMAG0156.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_I02_R1_IMAG0713.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  36

Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_J02_R1_IMAG0569.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_J02_R1_IMAG0570.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_J02_R1_IMAG0570.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_J02_R2_IMAG0024.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_J02_R2_IMAG0024.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_J02_R2_IMAG0025.JPG
Resized Cropped Image Width:  51

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0340.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0342.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0342.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0350.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0350.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG0351.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  36

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG1485.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG1522.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG1522.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG1524.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG1524.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_K03_R1_IMAG1525.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  36

Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_N05_R2_IMAG0351.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_N05_R2_IMAG1053.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_N05_R2_IMAG1053.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_N05_R2_IMAG1055.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_N05_R2_IMAG1055.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\impala\SER_S11_N05_R2_IMAG1056.JP

In [24]:
#function call
image_resizer(zebraFolder+"\\*.JPG")

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0543.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0543.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0550.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0550.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0551.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0551.JPG
Orig

Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0871.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0992.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG0992.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1001.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1001.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1022.JPG
Resi

Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1675.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1720.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1720.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1723.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1723.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R1_IMAG1728.JPG
Resi

Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R2_IMAG0057.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R2_IMAG0058.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R2_IMAG0058.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R2_IMAG0059.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R2_IMAG0059.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E02_R2_IMAG0062.JPG
Resi

Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E03_R1_IMAG0344.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E03_R1_IMAG0433.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E03_R1_IMAG0433.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E03_R1_IMAG0563.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E03_R1_IMAG0563.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_E03_R1_IMAG1312.JPG
Resi

...

Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_O13_R2_IMAG0392.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_O13_R2_IMAG0419.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_O13_R2_IMAG0419.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_O13_R2_IMAG0495.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_O13_R2_IMAG0495.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_O13_R2_IMAG0512.JPG
Resized Cropped Image Width:  512
Resi

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1788.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1810.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1810.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1816.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1816.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P06_R2_IMAG1888.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Over

Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1109.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1115.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1115.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1164.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1164.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_P13_R2_IMAG1183.JPG
Resized Cropped Image Width:  512
Resi

Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q05_R2_IMAG0366.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q05_R2_IMAG0366.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q05_R2_IMAG0397.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q05_R2_IMAG0397.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q05_R2_IMAG0402.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_Q05_R2_IMAG0402.JPG
Orig

Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_R08_R2_IMAG0318.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_R08_R2_IMAG0538.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_R08_R2_IMAG0538.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_R08_R2_IMAG0630.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Overwritten Resized Cropped Image are stored at Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_R08_R2_IMAG0630.JPG
Original Image Location:  C:\Users\17637\Desktop\AI_Project_Big_Cat\imageDataset\zebra\SER_S11_R08_R2_IMAG0878.JPG
Resized Cropped Image Width:  512
Resized Cropped Image Height:  361
Over